<a href="https://colab.research.google.com/github/el-danieel/predicao-de-disturbios-do-sono-com-IA/blob/main/Projeto.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#Download do dataset

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
base_dir = '/content/drive/MyDrive/Daniel Ferreira Pinheiro da Silva'#@param

In [ ]:
baixar_dataset = "Não" #@param ['Sim', "Não"]
if(baixar_dataset == "Sim"):
  for i in range(1,100+1,1):
    download_link = f"http://dataset.isr.uc.pt/ISRUC_Sleep/subgroupI/{i}.rar"
    download_dir = base_dir+"/dataset/ISRUC-SLEEP"
    !wget $download_link -P $download_dir

In [ ]:
#Dependências
import pandas as pd
pd.options.plotting.backend = "plotly"
from sklearn.utils import shuffle
import numpy as np

In [ ]:
dataset_dir = base_dir+'/dataset/Details_subgroup_I_Submission.xlsx'
df = pd.read_excel(dataset_dir)
df = df.iloc[1:]
df.columns = df.iloc[0]  # Usa a primeira linha restante como cabeçalho
df = df[1:]  # Remove a linha que agora é o cabeçalho
df.reset_index(drop=True, inplace=True)
df.replace('?', np.nan, inplace=True)
# Remove linhas onde a coluna 'age' é NaN
df = df.dropna(subset=['Age'])
#df = df.drop(columns=["Person ID", "Occupation"])
df = df[['Subject','Age','Sex','Diagnosis','Date of recording']]
df

1   Subject   Age Sex                     Diagnosis    Date of recording
0         1  64.0   M                          SAOS           18/5/2009 
1         2  52.0   M                          SAOS  2009-08-06 00:00:00
2         3  38.0   M  REM Sleep Behaviour Disorder            21/5/2009
3         4  27.0   M                         SRVAS            18/6/2009
4         5  58.0   F                          SAOS           25/5/2009 
..      ...   ...  ..                           ...                  ...
95       96  64.0   M                          SAOS            16/3/2012
96       97  66.0   F                          SAOS            16/3/2012
97       98  39.0   M                    RONCOPATIA           23/3/2012 
98       99  36.0   M                          SAOS            27/1/2012
99      100  65.0   M                          SAOS            27/3/2012

[98 rows x 5 columns]

Vamos trabalhar com pacientes onde: <br>
* Idade: 20~79<br>
* Diagnósticos: <a href="https://drauziovarella.uol.com.br/doencas-e-sintomas/apneia-obstrutiva-do-sono-saos/#:~:text=Apneia%20obstrutiva%20do%20sono%20(SAOS)%20é%20uma%20parada%20respiratória%20provocada,passagem%20de%20ar%20pela%20faringe.">SAOS</a>, D. Afectiva, Roncopatia<br>

In [ ]:
df = df[(df['Age'] >= 20) & (df['Age'] <= 79)]
df = df[(df['Diagnosis'] == 'SAOS') | (df['Diagnosis'] == 'D. Afectiva') | (df['Diagnosis'] == 'RONCOPATIA')]
display(df)
for coluna in ['Age','Sex','Diagnosis']:
  display(df[coluna].hist())

1   Subject   Age Sex   Diagnosis    Date of recording
0         1  64.0   M        SAOS           18/5/2009 
1         2  52.0   M        SAOS  2009-08-06 00:00:00
4         5  58.0   F        SAOS           25/5/2009 
6         7  70.0   M        SAOS  2009-01-06 00:00:00
7         8  76.0   M        SAOS  2009-01-06 00:00:00
..      ...   ...  ..         ...                  ...
95       96  64.0   M        SAOS            16/3/2012
96       97  66.0   F        SAOS            16/3/2012
97       98  39.0   M  RONCOPATIA           23/3/2012 
98       99  36.0   M        SAOS            27/1/2012
99      100  65.0   M        SAOS            27/3/2012

[83 rows x 5 columns]

Uma Epoch = 30 segundos

In [ ]:
#Todos os pacientes que vamos trabalhar
subject_list = df['Subject'].tolist()
info_values = df[['Age','Sex','Diagnosis']].T.to_dict()
print(len(subject_list))
print(subject_list)

83
[1, 2, 5, 7, 8, 9, 10, 13, 14, 15, 16, 17, 18, 19, 20, 21, 23, 24, 25, 26, 27, 28, 29, 30, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 49, 50, 51, 52, 53, 54, 55, 56, 58, 59, 60, 61, 63, 64, 65, 68, 69, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 87, 88, 89, 90, 91, 93, 94, 96, 97, 98, 99, 100]


Events: a list of abbreviations:
* L Out: Lights turn off
* L ON: Lights turn on
* MChg: Montage Change
* PLM: Periodic Leg Movement: motion that recurs over and over and the period of time required for each recurrence remains the same
* Awake: Awakening
* CH: Central Hypopnea
* CA: Central Apnea
* LM: Leg Movement
* MP: Movement Periodic
* OH: Obstructive Hypopnea
* OA: Obstructive Apnea
* REM, Aw: Awakening in REM
* AR: Arousal, abrupt change from sleep to wakefulness, or from a "deeper" stage of nonREM sleep to a "lighter" stage.
* MH: Mixed Hypopnea (a) - shallow breathing in which the air flow in and out of the airway is less than half of normal--usually associated with oxygen desaturation

<br>
MChg, L Out e L ON são intervenções humanas, vamos descartar as linhas que possuem esses valores junto dos próximos 2 minutos (2 min = 120 sec = 4 linhas)

In [ ]:
HUMAM_INTERFERENCE = ['MChg', 'L Out', 'L On']

In [ ]:
import re

def fix_hr_events(df):
  for index, row in df.iterrows():
    value = None
    if(any(char.isdigit() for char in str(row['Events']))):
      value = str(row['Events'])
    elif(any(char.isalpha() for char in str(row['HR']))):
      value = str(row['HR'])

    if value is not None:  # Verifica se o valor em 'HR' não é apenas um número
      # Separa o número (HR) do restante (eventos)
      match = re.match(r'(\d+)(.*)', value)
      if match:
        hr, events = match.groups()
        df.at[index, 'HR'] = int(hr)  # Atualiza 'HR' com o número
        # Adiciona os eventos à coluna 'Events' (se houver)
        if events:
          df.at[index, 'Events'] = events.strip()
        else:
          df.at[index, 'Events'] = np.nan
  return df

# Função para dividir eventos e criar colunas one-hot
def process_events(df):
  df.replace('REM Aw', 'REM,Awake', inplace=True)
  all_events = set()
  for index, row in df.iterrows():
    events = str(row['Events']).split(',')
    for event in events:
      event = event.strip()
      if event:
        all_events.add(event)

  for event in all_events:
    df[f'{event}'] = 0

  for index, row in df.iterrows():
    events = str(row['Events']).split(',')
    for event in events:
      event = event.strip()
      if event:
        df.at[index, f'{event}'] = 1
  df = df.drop(columns=['Events'])
  return df

# Função para fatiar o DataFrame com base em 'L Out' e 'L ON', ignorando fatias vazias
def slice_dataframe(df):
  if df.empty:
    return []  # Retorna uma lista vazia se o DataFrame for vazio

  dfs = []
  start_index = 0
  for i in range(len(df)):
    if any([df.iloc[i][v] for v in HUMAM_INTERFERENCE if v in df]):
      slice_ = df.iloc[start_index:i]
      if not slice_.empty:  # Verifica se a fatia não está vazia
        dfs.append(slice_)
      start_index = i + 4  # Pula as próximas 4 linhas (2 minutos)

  # Adiciona o último pedaço do DataFrame, se houver e não for vazio
  if len(df) and start_index < len(df):
    slice_ = df.iloc[start_index:]
    if not slice_.empty:
      dfs.append(slice_)

  return dfs

dataset_dir = base_dir+'/dataset/ISRUC-SLEEP/'
lista_dataset = []
for paciente_id in subject_list:
  print(f"Processando paciente {paciente_id}")
  for ds_index in [1,2]:
    df = pd.read_excel(dataset_dir+f'/{paciente_id}/{paciente_id}_{ds_index}.xlsx')
    df = df.rename(columns={'hich':'Epoch'})
    df = df[['Epoch','Stage','SpO2','HR','Events']]
    df = df.dropna(subset=['Epoch'])
    df_processed = process_events(fix_hr_events(df.copy()))
    df_processed['Subject'] = paciente_id
    df_processed['Dataset'] = ds_index
    for col in info_values[paciente_id-1]:
      df_processed[col] = info_values[paciente_id-1][col]
    lista_dataset += slice_dataframe(df_processed.copy())

Processando paciente 1
Processando paciente 2
Processando paciente 5
Processando paciente 7
Processando paciente 8
Processando paciente 9
Processando paciente 10
Processando paciente 13
Processando paciente 14
Processando paciente 15
Processando paciente 16
Processando paciente 17
Processando paciente 18
Processando paciente 19
Processando paciente 20
Processando paciente 21
Processando paciente 23
Processando paciente 24
Processando paciente 25
Processando paciente 26
Processando paciente 27
Processando paciente 28
Processando paciente 29
Processando paciente 30
Processando paciente 32
Processando paciente 33
Processando paciente 34
Processando paciente 35
Processando paciente 36
Processando paciente 37
Processando paciente 38
Processando paciente 39
Processando paciente 40
Processando paciente 41
Processando paciente 42
Processando paciente 43
Processando paciente 44
Processando paciente 45
Processando paciente 46
Processando paciente 47
Processando paciente 49
Processando paciente 5

In [ ]:
EVENTOS = ['OH', 'AR', 'REM', 'Awake', 'MH', 'OA', 'CH', 'PLM',  'nan', 'L Out', 'L On']

In [ ]:
#@title Estatísticas do conjunto de dados

for i in range(len(lista_dataset)):
  lista_dataset[i] = lista_dataset[i].drop(columns=['CSBr',  'MA', 'MChg', 'CA', 'LM','PVC', 'PAC','Per Slp', 'SN', 'UD1', 'Desat'],errors='ignore')
  lista_dataset[i].replace('n2','N2', inplace=True)
full_data = pd.concat(lista_dataset)
# Cria uma lista para armazenar os eventos de cada linha
event_lists = []

event_stats = full_data.copy()

# Itera sobre as linhas do DataFrame
for _, row in event_stats.iterrows():
  events = []
  for col in EVENTOS:
    if row[col] == 1:
      events.append(col)
  event_lists.append(','.join(events))  # Junta os eventos em uma string separada por vírgulas

# Adiciona a nova coluna 'events' ao DataFrame
event_stats['events'] = event_lists

# Remove as colunas antigas de one-hot encoding
event_stats = event_stats.drop(columns=EVENTOS)

# Exibe o DataFrame resultante

from collections import defaultdict

event_counts = defaultdict(int)

for _, row in event_stats.iterrows():
  events = row['events'].split(',')
  for event in events:
    if(event == ''):
      continue
    event_counts[event.strip()] += 1

# Cria um DataFrame a partir do dicionário de contagem de eventos
event_counts_df = pd.DataFrame.from_dict(event_counts, orient='index', columns=['Count'])

# Plota o histograma
fig = event_counts_df.plot.bar(y='Count', title='Event Distribution')
fig.show()
display(full_data['Stage'].hist())

# Cria colunas one-hot para a coluna 'Stage'
for i in range(len(lista_dataset)):
  lista_dataset[i] = pd.get_dummies(lista_dataset[i], columns=['Stage'])
  lista_dataset[i] = lista_dataset[i].replace({True: 1, False: 0})
  for evento in EVENTOS:
    if evento not in lista_dataset[i].columns:
      lista_dataset[i][evento] = 0

In [ ]:
import os
criar_dataset = 'Não' #@param ['Sim', 'Não']
if(not os.path.isfile(base_dir+'/dataset/dataset_final.csv')):
  criar_datatset = 'Sim'
def concatenate_rows(df, n=4):
  rows_list = []
  for i in range(0, len(df)-n-1):
    group = df.iloc[i: i + n]
    new_row = {}
    for col in df.columns:
      if(col in ['Epoch','L Out','L On', 'Subject', 'Dataset', 'Age', 'Sex', 'Diagnosis']):
        continue
      new_row.update({f"{col}_{j}": val for j, val in enumerate(group[col].values)})

    for value in ['Age', 'Sex', 'Diagnosis']:
      new_row[value] = df[value].iloc[0]
    for ev in EVENTOS:
      new_row[f'Target_{ev}'] = df.iloc[i+n+1][ev]
    rows_list.append(new_row)
  return pd.DataFrame(rows_list)

if(criar_dataset == 'Sim'):
  print("Criando o dataset")
  # Aplica a função a cada DataFrame na lista
  new_datasets = [concatenate_rows(df) for df in lista_dataset]
  # Concatena todos os novos DataFrames em um único
  final_df = pd.concat(new_datasets)
  final_df.replace(np.nan, 0, inplace=True)
  final_df.to_csv(base_dir+'/dataset/dataset_final.csv', index=False)
else:
  final_df = pd.read_csv(base_dir+'/dataset/dataset_final.csv')

In [ ]:
#Vamos embaralhar o dataset
final_df = shuffle(final_df)
df_encoded = final_df.copy()

#Como genero biológico só pode ser masculino ou feminino, essa coluna se torna binária (0/1)
df_encoded['Sex'] = df_encoded['Sex'].map({'M': 0, 'F': 1})

df_encoded = df_encoded.drop(columns=['Target_L On','Target_L Out', 'Target_nan']) #nan = Sem evento, ou seja, tudo 0

targets = ['Target_'+v for v in EVENTOS[:-3]]

# Itera sobre as linhas do DataFrame
event_lists = []
for _, row in final_df.iterrows():
  events = []
  for col in EVENTOS[:-3]:
    if row['Target_'+col] == 1:
      events.append(col)
  event_lists.append(','.join(events))  # Junta os eventos em uma string separada por vírgulas
# Adiciona a nova coluna 'events' ao DataFrame
final_df['events'] = event_lists

#Dropando colunas que não serão utilizadas (Sleeping Disorder pois será usada em outra parte e Blood Pressure pois a partir dela foram criadas outras 2)
df_encoded.drop(columns=targets+['Diagnosis'], inplace=True)

pd.set_option('display.max_columns', None)

features = df_encoded.columns.values
classes = final_df['events']
output_targets = final_df[targets]

n_classes = len(targets)

nome_dos_rotulos = {i:v for i,v in enumerate(targets)}
print("Nome das classes:", nome_dos_rotulos)

n_classes = len(targets)

entradas = df_encoded[features]

#Normaliza: transforma os números entre 0~1
for feature in features:
  entradas[feature] = (entradas[feature]-entradas[feature].min())/(entradas[feature].max()-entradas[feature].min())

n_entradas = entradas.shape[0]
#Observação: Entradas = Entries, não confundir com Inputs!!
print("Número de entradas: %d"%n_entradas)


Nome das classes: {0: 'Target_OH', 1: 'Target_AR', 2: 'Target_REM', 3: 'Target_Awake', 4: 'Target_MH', 5: 'Target_OA', 6: 'Target_CH', 7: 'Target_PLM'}
Número de entradas: 147202


In [ ]:
#@title Antigo
'''
sayo_datatset = base_dir+'/dataset/SaYoPillow.csv'
ss_dataset = base_dir+'/dataset/ss.csv'





#Conteudo do dataset
df = pd.read_csv(ss_dataset, sep=',')
df = df.fillna({'Sleep Disorder':'Healthy'}) #Dados com "NaN" são considerados "Saudáveis" (healthy)
#Person ID não é uma variável para ser tratada,
#"Ocupação" está sendo removido pois restringe as análises a este grupo de pessoas
df = df.drop(columns=["Person ID", "Occupation"])
df





df['Sleep Disorder'].hist(title="Distribuição das amostras de distúrbio do sono")



#Vamos embaralhar o dataset
df = shuffle(df)
df_encoded = df.copy()

#Separando as strings da coluna de pressão sanguínea em duas colunas separadas com números inteiros para a pressão sanguínea sistólica e diastólica
df_encoded[['Systolic Blood Pressure', 'Diastolic Blood Pressure']] = df_encoded['Blood Pressure'].str.split('/', expand=True)
df_encoded[['Systolic Blood Pressure', 'Diastolic Blood Pressure']] = df_encoded[['Systolic Blood Pressure', 'Diastolic Blood Pressure']].astype(int)

#Como genero biológico só pode ser masculino ou feminino, essa coluna se torna binária (0/1)
df_encoded['Gender'] = df_encoded['Gender'].map({'Male': 0, 'Female': 1})

#Dropando colunas que não serão utilizadas (Sleeping Disorder pois será usada em outra parte e Blood Pressure pois a partir dela foram criadas outras 2)
df_encoded.drop(columns=['Sleep Disorder', 'Blood Pressure'], inplace=True)

#Dummy encoding (transforma a coluna que armazena variáveis categóricas em colunas booleanas para cada categoria)
colunas_string = df_encoded.select_dtypes(include='object').columns
print("Colunas para dummy encoding:", colunas_string)
df_encoded = pd.get_dummies(df_encoded, columns=colunas_string, dtype=int)

pd.set_option('display.max_columns', None)

features = df_encoded.columns.values
classes = df['Sleep Disorder']

rotulos_distintos = list(set(classes.to_list()))

nome_dos_rotulos = {i:v for i,v in enumerate(pd.get_dummies(df['Sleep Disorder']).columns)}
print("Nome das classes:", nome_dos_rotulos)

rotulo_numero = [rotulos_distintos.index(classe) for classe in classes]

rotulo_vetor = [( [ 1. if rotulos_distintos.index(classe) == i else 0 for i in range(0,len(rotulos_distintos)) ] ) for classe in classes]

n_classes = len(rotulos_distintos)

entradas = df_encoded[features]

#Normaliza: transforma os números entre 0~1
for feature in features:
  entradas[feature] = (entradas[feature]-entradas[feature].min())/(entradas[feature].max()-entradas[feature].min())
entradas

n_entradas = entradas.shape[0]
#Observação: Entradas = Entries, não confundir com Inputs!!
print("Número de entradas: %d"%n_entradas)
'''

'\nsayo_datatset = base_dir+\'/dataset/SaYoPillow.csv\'\nss_dataset = base_dir+\'/dataset/ss.csv\'\n\n\n\n\n\n#Conteudo do dataset\ndf = pd.read_csv(ss_dataset, sep=\',\')\ndf = df.fillna({\'Sleep Disorder\':\'Healthy\'}) #Dados com "NaN" são considerados "Saudáveis" (healthy)\n#Person ID não é uma variável para ser tratada,\n#"Ocupação" está sendo removido pois restringe as análises a este grupo de pessoas\ndf = df.drop(columns=["Person ID", "Occupation"])\ndf\n\n\n\n\n\ndf[\'Sleep Disorder\'].hist(title="Distribuição das amostras de distúrbio do sono")\n\n\n\n#Vamos embaralhar o dataset\ndf = shuffle(df)\ndf_encoded = df.copy()\n\n#Separando as strings da coluna de pressão sanguínea em duas colunas separadas com números inteiros para a pressão sanguínea sistólica e diastólica\ndf_encoded[[\'Systolic Blood Pressure\', \'Diastolic Blood Pressure\']] = df_encoded[\'Blood Pressure\'].str.split(\'/\', expand=True)\ndf_encoded[[\'Systolic Blood Pressure\', \'Diastolic Blood Pressure\']] = 

In [ ]:
#@title Correlação dos dados

import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go

#f, ax = plt.subplots(figsize=(10, 8))
corr = df_encoded.corr(numeric_only = True)
#sns.heatmap(corr, square=True, ax=ax)

# Create the heatmap
fig = go.Figure(data=go.Heatmap(
    z=corr.values,
    x=corr.columns,
    y=corr.index,
    colorscale='magma', #Cores: https://plotly.com/python/builtin-colorscales/
    text=corr.values.round(4),
    texttemplate='%{text}',
))

# Update the layout
fig.update_layout(
    font=dict(size=15),
    width=1200,
    height=1200,
)

# Show the heatmap
fig.show()


KFold Validation: https://machinelearningmastery.com/k-fold-cross-validation/
<br>Dataset não balanceado: https://developers.google.com/machine-learning/data-prep/construct/sampling-splitting/imbalanced-data?hl=pt-br

In [ ]:
#como nosso dataset não é balencado, isto é, as classes não possuem distribuições
#iguais (não ter disturbio de sono é maior que as outras duas), precisamos garantir
#que os datasets de treino e teste possuam a mesma quantidade de informações
#para cada classe.

from sklearn.model_selection import StratifiedKFold

# Define the number of folds
n_folds = 5

# Initialize the StratifiedKFold object
skf = StratifiedKFold(n_splits=n_folds, shuffle=True)

datasets = []
# Split the dataset into folds
for i, (train_index, test_index) in enumerate(skf.split(entradas, classes)):
    # Print the fold number
    print(f">Fold {i + 1}:")
    datasets.append({'treino':{}, 'teste':{}})
    # Get the training and testing data
    datasets[-1]['treino']['entrada'], datasets[-1]['teste']['entrada'] = entradas.iloc[train_index], entradas.iloc[test_index]
    datasets[-1]['treino']['rotulo'], datasets[-1]['teste']['rotulo'] = output_targets.iloc[train_index], output_targets.iloc[test_index]

    for ds in ['treino', 'teste']:
      print(f"\t- Qtd. {ds}:\t{len(datasets[-1][ds]['entrada'])}")

    for ds in ['treino', 'teste']:
      print(f"\t- Distribuição do dataset {ds}:\t{datasets[-1][ds]['rotulo'].value_counts().to_dict()}")


    datasets[-1]['treino']['entrada'], datasets[-1]['teste']['entrada'] = entradas.iloc[train_index].to_numpy().astype(float), entradas.iloc[test_index].to_numpy().astype(float)
    datasets[-1]['treino']['rotulo'], datasets[-1]['teste']['rotulo'] = output_targets.iloc[train_index].to_numpy().astype(float), output_targets.iloc[test_index].to_numpy().astype(float)


/usr/local/lib/python3.10/dist-packages/sklearn/model_selection/_split.py:737: UserWarning:

The least populated class in y has only 1 members, which is less than n_splits=5.



>Fold 1:
	- Qtd. treino:	117761
	- Qtd. teste:	29441
	- Distribuição do dataset treino:	{(0, 0, 0, 0, 0, 0, 0, 0): 94855, (0, 1, 0, 0, 0, 0, 0, 0): 12967, (0, 0, 0, 1, 0, 0, 0, 0): 2467, (1, 0, 0, 0, 0, 0, 0, 0): 1892, (0, 0, 0, 0, 0, 0, 0, 1): 1454, (0, 1, 0, 0, 1, 0, 0, 0): 796, (0, 0, 0, 0, 1, 0, 0, 0): 749, (0, 0, 0, 0, 0, 1, 0, 0): 710, (1, 1, 0, 0, 0, 0, 0, 0): 635, (0, 1, 0, 0, 0, 0, 0, 1): 290, (0, 1, 0, 0, 0, 1, 0, 0): 202, (0, 0, 0, 1, 1, 0, 0, 0): 124, (1, 0, 0, 1, 0, 0, 0, 0): 116, (0, 0, 1, 1, 0, 0, 0, 0): 91, (0, 0, 0, 0, 0, 0, 1, 0): 77, (0, 0, 0, 1, 0, 1, 0, 0): 67, (0, 1, 0, 1, 0, 0, 0, 0): 52, (0, 0, 0, 1, 0, 0, 0, 1): 32, (0, 1, 0, 0, 1, 0, 0, 1): 31, (1, 0, 0, 0, 0, 0, 0, 1): 28, (0, 0, 0, 0, 0, 0, 1, 1): 20, (0, 0, 0, 0, 1, 0, 0, 1): 20, (1, 0, 0, 0, 0, 1, 0, 0): 20, (1, 1, 0, 0, 0, 0, 0, 1): 18, (0, 1, 0, 0, 0, 0, 1, 0): 11, (0, 0, 0, 0, 0, 1, 0, 1): 9, (1, 1, 0, 0, 1, 0, 0, 0): 5, (1, 1, 0, 0, 0, 1, 0, 0): 5, (1, 0, 0, 0, 1, 0, 0, 0): 4, (0, 1, 0, 1, 0, 0, 0, 1):

In [ ]:
#Dependências
from tensorflow import keras
from keras import models, layers

In [ ]:
import pickle
'''
pickle.dump(datasets, open('datasets.pkl', 'wb'))
params = {}
for v in ['nome_dos_rotulos','n_classes','output_targets','targets','features']:
  params[v] = eval(f"{v}")
pickle.dump(params, open('params.pkl', 'wb'))
'''
datasets = pickle.load(open(base_dir+'/datasets.pkl', 'rb'))
params = pickle.load(open(base_dir+'/params.pkl', 'rb'))

for param in params:
    exec(f"{param} = params['{param}']")

In [ ]:
# Tamanho da entrada
input_shape = (len(features),)
print('Tamanho da entrada: %d informações (caracteristicas)'%input_shape)

# Categorias a serem classificadas
print("Número de rótulos (categorias/classes): %d - "%n_classes,targets)

Tamanho da entrada: 74 informações (caracteristicas)
Número de rótulos (categorias/classes): 8 -  ['Target_OH', 'Target_AR', 'Target_REM', 'Target_Awake', 'Target_MH', 'Target_OA', 'Target_CH', 'Target_PLM']


In [ ]:
def mlp_sintaxe1(input_shape, output_classes, ativacao = 'sigmoid'):
  model = keras.Sequential()
  model.add(layers.Input(input_shape))
  model.add(layers.Dense(1024, activation='relu'))
  model.add(layers.Dropout(0.35))
  model.add(layers.Dense(1024, activation='relu'))
  model.add(layers.Dropout(0.35))
  model.add(layers.Dense(512, activation='relu'))
  model.add(layers.Dropout(0.35))
  model.add(layers.Dense(512, activation='relu'))
  model.add(layers.Dropout(0.35))
  model.add(layers.Dense(256, activation='relu'))
  model.add(layers.Dropout(0.35))
  model.add(layers.Dense(64, activation='relu'))
  model.add(layers.Dropout(0.35))
  model.add(layers.Dense(64, activation='relu'))
  model.add(layers.Dense(output_classes, activation=ativacao))
  return model

In [ ]:
model = mlp_sintaxe1(input_shape, n_classes)
model.summary()
#keras.utils.plot_model(model, show_shapes=True)

Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                         ┃ Output Shape                ┃         Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━┩
│ dense (Dense)                        │ (None, 1024)                │          76,800 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dropout (Dropout)                    │ (None, 1024)                │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_1 (Dense)                      │ (None, 1024)                │       1,049,600 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dropout_1 (Dropout)                  │ (None, 1024)                │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_2 (Dense)                      │ (None, 512)                 │         524,800 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dropout_2 (Dropout)                  │ (None, 512)                 │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_3 (Dense)                      │ (None, 512)                 │         262,656 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dropout_3 (Dropout)                  │ (None, 512)                 │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_4 (Dense)                      │ (None, 256)                 │         131,328 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dropout_4 (Dropout)                  │ (None, 256)                 │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_5 (Dense)                      │ (None, 64)                  │          16,448 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dropout_5 (Dropout)                  │ (None, 64)                  │               0 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_6 (Dense)                      │ (None, 64)                  │           4,160 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense_7 (Dense)                      │ (None, 8)                   │             520 │
└──────────────────────────────────────┴─────────────────────────────┴─────────────────┘

 Total params: 2,066,312 (7.88 MB)

 Trainable params: 2,066,312 (7.88 MB)

 Non-trainable params: 0 (0.00 B)

In [ ]:
import tensorflow
from tensorflow.keras.metrics import Precision, Recall
from tensorflow.keras.callbacks import Callback

# Treina para cada fold
historico = []
pred_true_folds = []

for i, ds in enumerate(datasets):
  # Treina o modelo
  model = mlp_sintaxe1(input_shape, n_classes)
  optimizer = tensorflow.keras.optimizers.Adam(learning_rate=1e-7)
  model.compile(loss='binary_crossentropy', optimizer=optimizer,
                metrics=[keras.metrics.Precision(), keras.metrics.Recall()]
                #metrics=[keras.metrics.Precision(class_id = _, name = f"{nome[7:]} Prec.") for _,nome in nome_dos_rotulos.items()] + \
                #        [keras.metrics.Recall(class_id = _, name = f"{nome[7:]} Rec.") for _,nome in nome_dos_rotulos.items()]
                )
  '''
  history = model.fit(ds['treino']['entrada'],
                      ds['treino']['rotulo'],
                      class_weight=class_weight_dict,
                      epochs=3000,
                      batch_size=16,
                      verbose=1,
                      validation_split=0.2)
  historico.append(history)
  '''
  model.load_weights(base_dir+f'/fold_{i}.h5')
  # Avalia o modelo
  y_pred = model.predict(ds['teste']['entrada'])
  y_true = ds['teste']['rotulo']

  pred_true_folds.append((y_pred,y_true))

921/921 ━━━━━━━━━━━━━━━━━━━━ 5s 3ms/step
921/921 ━━━━━━━━━━━━━━━━━━━━ 2s 2ms/step
920/920 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step
920/920 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step
920/920 ━━━━━━━━━━━━━━━━━━━━ 2s 2ms/step


In [ ]:
# Plota os históricos
for i, h in enumerate(historico):
  plt.figure(figsize=(12, 6))
  plt.plot(h.history['loss'], label=f'Fold {i+1} - treino')
  plt.plot(h.history['val_loss'], label=f'Fold {i+1} - teste')
  plt.xlabel('Épocas')
  plt.ylabel('Perda')
  plt.legend()
  plt.show()
  '''
  for k in [k for k in h.history.keys() if 'val_' != k[:4] and k != 'loss']:
    plt.plot(h.history[k], label=f'Fold {i+1} - treino - {k}')
    plt.plot(h.history['val_'+k], label=f'Fold {i+1} - teste - {k}')
  plt.xlabel('Épocas')
  plt.ylabel('Perda')
  plt.legend()
  plt.show()
  '''

In [ ]:
import numpy as np
from sklearn.metrics import roc_curve, auc
import plotly.graph_objects as go
from itertools import cycle

# Número de classes
n_classes = pred_true_folds[0][1].shape[1]
n_folds = len(pred_true_folds)

# Inicializa os dicionários para armazenar FPR, TPR e AUC para cada fold e classe
fpr = {i: {} for i in range(n_classes)}
tpr = {i: {} for i in range(n_classes)}
roc_auc = {i: {} for i in range(n_classes)}

# Calcula as curvas ROC e AUC para cada fold e classe
for fold_idx, (y_pred, y_true) in enumerate(pred_true_folds):
    for i in range(n_classes):
        fpr[i][fold_idx], tpr[i][fold_idx], _ = roc_curve(y_true[:, i], y_pred[:, i])
        roc_auc[i][fold_idx] = auc(fpr[i][fold_idx], tpr[i][fold_idx])

# Plotando as curvas ROC para cada classe
for i in range(n_classes):
    fig = go.Figure()
    for fold_idx in range(n_folds):
        fig.add_trace(go.Scatter(x=fpr[i][fold_idx], y=tpr[i][fold_idx], mode='lines',
                                 name=f'Fold {fold_idx+1} (AUC = {roc_auc[i][fold_idx]:.2f})'))
    fig.add_trace(go.Scatter(x=[0, 1], y=[0, 1], mode='lines', name='Linha Aleatória', line=dict(color='black', dash='dash')))

    fig.update_layout(
        title=f'Curvas ROC para Classe `{nome_dos_rotulos[i]}`',
        xaxis_title='Falsos Positivos (FPR)',
        yaxis_title='Verdadeiros Positivos (TPR)',
        showlegend=True,
        legend=dict(x=0.8, y=0.1)
    )

    fig.show()